# Coursera IBM Data Science Professional Capstone Project

# Leveraging Foursquare API and Hamilton Neighbourhood Dataset for Auto-workshop location 
 ## Report written by Abiola D. Obembe
   ### Date: 23-01-2020

# 1.	Introduction

## 1.1 Background


Hamilton is a port city in the Canadian province of Ontario. An industrialized city in the Golden Horseshoe at the west end of Lake Ontario, Hamilton has a population of 536,917, and its census metropolitan area, which includes Burlington and Grimsby, has a population of 747,545. The city is 58 kilometres (36 mi) southwest of Toronto, with which the Greater Toronto and Hamilton Area (GTHA) is formed. On January 1, 2001, the current boundaries of Hamilton were created through the amalgamation of the original city with other municipalities of the Regional Municipality of Hamilton–Wentworth. Residents of the city are known as Hamiltonians. Since 1981, the metropolitan area has been listed as the ninth largest in Canada and the third largest in Ontario. With such a significant population lies opportunities and the potential for establishing businesses to cater for the populace. Take for instance, it will be beneficial for prospective entrepreneurs to be able to determine the type of business to establish and the best location to setup their office

## 1.2 Problem statement
After residing a few months in the city of Hamilton, a wealthy contractor has decided to establish a business in the local area. Based on his previous work experience in the auto industry, he has suggested that his preference will be to set up an auto business in Canada. However, after a careful study of the city, he is confident that establishing an automobile repair workshop will be profitable. However, he is unsure of the best location for his workshop. The aim of this project is to utilize available data from the city of Hamilton and Foursquare API to guide the contractor on choice location(s) to setup his workshop.


## 1.3 Interest

Using a data-driven approach to determine a business type, the best location(s) to setup businesses will be highly beneficial to Entrepreneurs as it ensures that their business will receive traction. In addition, this will help the government to develop the required infrastructure in such neighborhoods to attract more businesses which will increase employment and provide revenue for the government through taxes from businesses and people. 



# 2. Data Section

## 2.1 Data sources
Data to be employed for this project will be obtained from the city of Hamilton website from the site http://open.hamilton.ca/datasets/ac6fc684043341f6b1d6298c146a0bcf_1. Specifically, the webpage has data on the distinct municipal addresses in Hamilton. This dataset exists as both CSV files and GEOJSON files. Besides, the original dataset consists of 253,876 rows of data and 12 columns (features).  

In [1]:
# install libraries
import numpy as np
import pandas as pd
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)
! pip install geopy
from geopy.geocoders import Nominatim
import requests
import json
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
! pip install folium
import folium
print('Libraries installed!')

Libraries installed!


In [2]:
# Download and explore dataset
!wget -q -O 'hamilton_data.json' https://opendata.arcgis.com/datasets/ac6fc684043341f6b1d6298c146a0bcf_1.geojson


with open ('hamilton_data.json') as json_data :
      hamilton_data = json.load(json_data)
hamilton_dataset = hamilton_data['features'][0:100000]

hamilton_dataset

[{'type': 'Feature',
  'properties': {'OBJECTID': 1,
   'LONGITUDE': '-79.79023580613546',
   'LATITUDE': '43.20757090548786',
   'NUMBER_COMPLETE': '110',
   'UNIT_NUMBER_COMPLETE': None,
   'FULL_STREET_NAME': 'Hanover Place',
   'SETTLEMENT': None,
   'COMMUNITY': 'Hamilton',
   'MUNICIPALITY': 'City of Hamilton',
   'COUNTRY': 'Canada',
   'PROVINCE': 'Ontario'},
  'geometry': {'type': 'Point',
   'coordinates': [-79.7902392805614, 43.20757939303672]}},
 {'type': 'Feature',
  'properties': {'OBJECTID': 2,
   'LONGITUDE': '-79.75926619930769',
   'LATITUDE': '43.21327570171375',
   'NUMBER_COMPLETE': '49',
   'UNIT_NUMBER_COMPLETE': None,
   'FULL_STREET_NAME': 'Upper Lake Avenue',
   'SETTLEMENT': None,
   'COMMUNITY': 'Stoney Creek',
   'MUNICIPALITY': 'City of Hamilton',
   'COUNTRY': 'Canada',
   'PROVINCE': 'Ontario'},
  'geometry': {'type': 'Point',
   'coordinates': [-79.75926966441459, 43.21328419171143]}},
 {'type': 'Feature',
  'properties': {'OBJECTID': 3,
   'LONGITUDE':

In [3]:
# display lenth of dictionary hamilton_dataset
print('The length of the Hamilton dataset/dictionary is', len(hamilton_dataset))

The length of the Hamilton dataset/dictionary is 100000


In [4]:
# Create dataframe
column_names  =['ID','Address', 'Longitude', 'Latitude', 'Settlement', 'Community', 'Municipal']
neighborhoods = pd.DataFrame(columns= column_names)

for data in hamilton_dataset:
    neigh_ID = data['properties']['OBJECTID']
    neigh_latlon = data['geometry']['coordinates']
    neigh_lon = neigh_latlon[0]
    neigh_lat = neigh_latlon[1]
    neigh_add = data['properties']['FULL_STREET_NAME']
    neigh_comm = data['properties']['COMMUNITY']
    
    neighborhoods = neighborhoods. append({'ID': neigh_ID, 'Longitude': neigh_lon, 'Latitude': neigh_lat, 
                                           'Address' :  neigh_add, 'Community':neigh_comm}, ignore_index = True)
    
neighborhoods.head()

ID            Address  Longitude   Latitude  Settlement     Community  \
0  1      Hanover Place -79.790239  43.207579         NaN      Hamilton   
1  2  Upper Lake Avenue -79.759270  43.213284         NaN  Stoney Creek   
2  3       Orr Crescent -79.709277  43.209003         NaN  Stoney Creek   
3  4  Concession 8 West -80.013807  43.380473         NaN   Flamborough   
4  5        Cooper Road -80.183338  43.340202         NaN   Flamborough   

   Municipal  
0        NaN  
1        NaN  
2        NaN  
3        NaN  
4        NaN

# 2.2 Sample of dataset for Analysis

In [5]:
# Quality check: Examine and clean dataframe
neighborhoods.dropna(axis=1, how='any', thresh=None, inplace=True)
print('The dataframe has {} communities in the city of Hamilton.'. format(len(neighborhoods['Community'].unique())))
print(neighborhoods.shape)
neighborhoods.head()

The dataframe has 7 communities in the city of Hamilton.
(100000, 5)


ID            Address  Longitude   Latitude     Community
0  1      Hanover Place -79.790239  43.207579      Hamilton
1  2  Upper Lake Avenue -79.759270  43.213284  Stoney Creek
2  3       Orr Crescent -79.709277  43.209003  Stoney Creek
3  4  Concession 8 West -80.013807  43.380473   Flamborough
4  5        Cooper Road -80.183338  43.340202   Flamborough

In [6]:
 # pandas drop columns with drop function and display unique communities

df = neighborhoods.groupby(['Address', 'Community'], as_index= False).first()

print('The dataframe has {} communities in the city of Hamilton.'. format(len(df['Community'].unique())))
print(df.shape)

The dataframe has 7 communities in the city of Hamilton.
(4056, 5)


In [7]:
# More information on dataframe
print(df['Community'].unique())
df.head()

['Flamborough' 'Ancaster' 'Hamilton' 'Glanbrook' 'Dundas' 'Stoney Creek'
 'Burlington']


Address    Community     ID  Longitude   Latitude
0  3rd Concession Road East  Flamborough  63379 -79.860544  43.346062
1               Abbey Close     Ancaster   4821 -80.001446  43.211121
2           Abbington Drive     Hamilton   3128 -79.905134  43.228994
3               Abbot Court     Hamilton  28830 -79.858676  43.223276
4               Abbot Drive     Hamilton  11971 -79.857134  43.225534

In [8]:
# Use geop library to get the latitude and longitude values of the city of Hamilton
address    = 'Hamilton, ON'
geolocator = Nominatim(user_agent ='hamilton_explorer')
location   = geolocator.geocode(address)
latitude   = location.latitude
longitude  = location.longitude

print ('The geographical coordinate of the city of Hamilton are {}, {}.'. format(latitude,longitude))

The geographical coordinate of the city of Hamilton are 43.255205, -79.868202.


In [9]:
# Create a map of the city of Hamilton with the communities superimposed 
map_hamilton = folium.Map(location = [latitude,longitude], zoom_start = 10)

# add makers to map
for lat, lng, label in zip(df['Latitude'][0:1000], df['Longitude'][0:1000], df['Address'][0:1000]):
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker([lat,lng], radius = 5, popup = label, color = 'green', fill = True, fill_color = '#3186cc',
                         fill_opacity = 0.7, parse_html = False). add_to(map_hamilton)

map_hamilton

In [10]:
# Let's explore the first neighborhood in the df dataframe
lati  = df.loc[0,'Latitude']
longi = df.loc[0,'Longitude']
addy  = df.loc[0,'Address']
 
print('Latitude and Longitude values of {} are {}, {}'. format(addy, lati, longi))

Latitude and Longitude values of 3rd Concession Road East are 43.346061745234074, -79.86054444128337


In [11]:
# The code was removed by Watson Studio for sharing.

Yor credentials:
CLIENT ID :CXH35QZUAPYVZ4IC2BEDC4F4KP2U1TRNVMCAPCGIHCNVNQOR
CLIENT_SECRET:RN4IMJLOJ5UF0JXWALLCLHN3MAXHG01NJBUZC5XKYNL5IHOG
Auto ------ OK!


In [12]:
# function to confirm/extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
    if len(categories_list)== 0:
        return None
    else:
        return categories_list[0]['name']

In [13]:
# We are going to explore all the addresses in the dataframe
# The function below repeats the above process to all addresses in the dataframe

def getNearbyVenues(names,latitudes,longitudes, radius = 500):
    venues_list =[]
    for name,lat,lng in zip(names,latitudes,longitudes):
        print(name)
        # create API request url
        url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'. format(CLIENT_ID, CLIENT_SECRET, VERSION,lat,lng,search_query,
                                                                                                                                    radius,LIMIT)
        results = requests.get(url).json()['response']['venues']
        
        venues_list.append([(name,lat,lng,
                         v['name'], v['location']['lat'], 
                         v['location']['lng'],v['categories']) for v in results])
                      
                    
    nearby_venues = pd.DataFrame( [item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Address', 'Address Latitude', 'Address Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Category']
    return (nearby_venues)


In [14]:
# Apply above function on each address and create new datframe called hamilton_Venues

hamilton_Venues = getNearbyVenues(names = df['Address'], latitudes = df['Latitude'], longitudes= df['Longitude'])

hamilton_Venues

3rd Concession Road East
Abbey Close
Abbington Drive
Abbot Court
Abbot Drive
Abbotsford Trail
Abel Court
Aberdeen Avenue
Aberdeen Avenue
Aberfoyle Avenue
Acacia Street
Academy Street
Acadia Drive
Ackland Street
Acorn Street
Acredale Drive
Ada Court
Adair Avenue North
Adair Avenue South
Adams Street
Adelaide Avenue
Adele Court
Adeline Avenue
Adis Avenue
Adler Avenue
Admiral Place
Adorn Court
Adriatic Boulevard
Afton Avenue
Agawam Court
Agincourt Avenue
Agnes Street
Aikman Avenue
Ainsley Road
Ainslie Avenue
Ainsworth Street
Aintree Court
Airdrie Avenue
Airport Road East
Airport Road West
Alanson Street
Alba Street
Albany Avenue
Albemarle Street
Albert Street
Albert Street
Albert Street
Alberton Road
Albion Falls Boulevard
Albright Road
Alconbury Drive
Alden Street
Alder Court
Aldercrest Avenue
Aldercrest Avenue
Alderlea Avenue
Alderney Avenue
Alderson Drive
Alderson Road
Aldgate Avenue
Aldridge Court
Aldridge Street
Alessio Drive
Alexander Road
Alexander Street
Alexsia Court
Alfrin Court

Address  Address Latitude  Address Longitude  \
0                  Abbot Court         43.223276         -79.858676   
1                  Abbot Court         43.223276         -79.858676   
2                  Abbot Drive         43.225534         -79.857134   
3                  Abbot Drive         43.225534         -79.857134   
4              Aberdeen Avenue         43.249750         -79.888410   
5              Aberdeen Avenue         43.249750         -79.888410   
6              Aberdeen Avenue         43.249750         -79.888410   
7               Academy Street         43.228072         -79.974561   
8               Ackland Street         43.200957         -79.793210   
9                 Acorn Street         43.252413         -79.844719   
10                Acorn Street         43.252413         -79.844719   
11          Adair Avenue South         43.230952         -79.791849   
12                Adams Street         43.255128         -79.846846   
13                Adams Street         43.255128         -79.846846   
14                Adams Street         43.255128         -79.846846   
15                Adams Street         43.255128         -79.846846   
16              Adeline Avenue         43.244363         -79.790673   
17              Adeline Avenue         43.244363         -79.790673   
18                Adler Avenue         43.194645         -79.845221   
19                Adler Avenue         43.194645         -79.845221   
20                Adler Avenue         43.194645         -79.845221   
21                Adler Avenue         43.194645         -79.845221   
22                Adler Avenue         43.194645         -79.845221   
23                Adler Avenue         43.194645         -79.845221   
24               Admiral Place         43.240623         -79.781542   
25               Admiral Place         43.240623         -79.781542   
26               Admiral Place         43.240623         -79.781542   
27                 Adorn Court         43.234503         -79.766155   
28                 Adorn Court         43.234503         -79.766155   
29                 Adorn Court         43.234503         -79.766155   
30                 Adorn Court         43.234503         -79.766155   
31                 Adorn Court         43.234503         -79.766155   
32                 Adorn Court         43.234503         -79.766155   
33          Adriatic Boulevard         43.210973         -79.709400   
34            Agincourt Avenue         43.254695         -79.810326   
35            Agincourt Avenue         43.254695         -79.810326   
36            Agincourt Avenue         43.254695         -79.810326   
37            Agincourt Avenue         43.254695         -79.810326   
38                Agnes Street         43.249391         -79.813309   
39                Agnes Street         43.249391         -79.813309   
40               Aikman Avenue         43.250208         -79.844438   
41               Aikman Avenue         43.250208         -79.844438   
42               Aintree Court         43.226520         -79.806283   
43              Airdrie Avenue         43.241079         -79.782540   
44              Airdrie Avenue         43.241079         -79.782540   
45              Airdrie Avenue         43.241079         -79.782540   
46              Alanson Street         43.246454         -79.854145   
47              Alanson Street         43.246454         -79.854145   
48               Albany Avenue         43.247195         -79.802870   
49               Albany Avenue         43.247195         -79.802870   
50               Albany Avenue         43.247195         -79.802870   
51            Albemarle Street         43.257115         -79.822368   
52            Albemarle Street         43.257115         -79.822368   
53            Albemarle Street         43.257115         -79.822368   
54            Albemarle Street         43.257115         -79.822368   
55            Albemarle Street         43.25711

In [15]:
# function to confirm/extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['Category']
    except:
        categories_list = row['venue.Category']
    if len(categories_list)== 0:
        return None
    else:
        return categories_list[0]['name']

In [16]:
# Let us filter the datframe and examine the shape of the new dataframe created
hamilton_Venues['Category']= hamilton_Venues.apply(get_category_type, axis = 1)
print(hamilton_Venues.shape)

(3215, 7)


In [17]:
# Let us inspect the final dataframe
hamilton_Venues


Address  Address Latitude  Address Longitude  \
0                  Abbot Court         43.223276         -79.858676   
1                  Abbot Court         43.223276         -79.858676   
2                  Abbot Drive         43.225534         -79.857134   
3                  Abbot Drive         43.225534         -79.857134   
4              Aberdeen Avenue         43.249750         -79.888410   
5              Aberdeen Avenue         43.249750         -79.888410   
6              Aberdeen Avenue         43.249750         -79.888410   
7               Academy Street         43.228072         -79.974561   
8               Ackland Street         43.200957         -79.793210   
9                 Acorn Street         43.252413         -79.844719   
10                Acorn Street         43.252413         -79.844719   
11          Adair Avenue South         43.230952         -79.791849   
12                Adams Street         43.255128         -79.846846   
13                Adams Street         43.255128         -79.846846   
14                Adams Street         43.255128         -79.846846   
15                Adams Street         43.255128         -79.846846   
16              Adeline Avenue         43.244363         -79.790673   
17              Adeline Avenue         43.244363         -79.790673   
18                Adler Avenue         43.194645         -79.845221   
19                Adler Avenue         43.194645         -79.845221   
20                Adler Avenue         43.194645         -79.845221   
21                Adler Avenue         43.194645         -79.845221   
22                Adler Avenue         43.194645         -79.845221   
23                Adler Avenue         43.194645         -79.845221   
24               Admiral Place         43.240623         -79.781542   
25               Admiral Place         43.240623         -79.781542   
26               Admiral Place         43.240623         -79.781542   
27                 Adorn Court         43.234503         -79.766155   
28                 Adorn Court         43.234503         -79.766155   
29                 Adorn Court         43.234503         -79.766155   
30                 Adorn Court         43.234503         -79.766155   
31                 Adorn Court         43.234503         -79.766155   
32                 Adorn Court         43.234503         -79.766155   
33          Adriatic Boulevard         43.210973         -79.709400   
34            Agincourt Avenue         43.254695         -79.810326   
35            Agincourt Avenue         43.254695         -79.810326   
36            Agincourt Avenue         43.254695         -79.810326   
37            Agincourt Avenue         43.254695         -79.810326   
38                Agnes Street         43.249391         -79.813309   
39                Agnes Street         43.249391         -79.813309   
40               Aikman Avenue         43.250208         -79.844438   
41               Aikman Avenue         43.250208         -79.844438   
42               Aintree Court         43.226520         -79.806283   
43              Airdrie Avenue         43.241079         -79.782540   
44              Airdrie Avenue         43.241079         -79.782540   
45              Airdrie Avenue         43.241079         -79.782540   
46              Alanson Street         43.246454         -79.854145   
47              Alanson Street         43.246454         -79.854145   
48               Albany Avenue         43.247195         -79.802870   
49               Albany Avenue         43.247195         -79.802870   
50               Albany Avenue         43.247195         -79.802870   
51            Albemarle Street         43.257115         -79.822368   
52            Albemarle Street         43.257115         -79.822368   
53            Albemarle Street         43.257115         -79.822368   
54            Albemarle Street         43.257115         -79.822368   
55            Albemarle Street         43.25711

In [18]:
# Let us also check how many venues were returned for each address
hamilton_Venues.groupby('Address').count()

Address Latitude  Address Longitude  Venue  \
Address                                                                
Abbot Court                              2                  2      2   
Abbot Drive                              2                  2      2   
Aberdeen Avenue                          3                  3      3   
Academy Street                           1                  1      1   
Ackland Street                           1                  1      1   
Acorn Street                             2                  2      2   
Adair Avenue South                       1                  1      1   
Adams Street                             4                  4      4   
Adeline Avenue                           2                  2      2   
Adler Avenue                             6                  6      6   
Admiral Place                            3                  3      3   
Adorn Court                              6                  6      6   
Adriatic Boulevard                       1                  1      1   
Agincourt Avenue                         4                  4      4   
Agnes Street                             2                  2      2   
Aikman Avenue                            2                  2      2   
Aintree Court                            1                  1      1   
Airdrie Avenue                           3                  3      3   
Alanson Street                           2                  2      2   
Albany Avenue                            3                  3      3   
Albemarle Street                         6                  6      6   
Albert Street                            2                  2      2   
Albion Falls Boulevard                   1                  1      1   
Aldercrest Avenue                        2                  2      2   
Alexander Street                         1                  1      1   
Algonquin Avenue                         1                  1      1   
Alice Street                             4                  4      4   
Allan Avenue                             8                  8      8   
Allandale Street                         4                  4      4   
Allegro Place                            3                  3      3   
Allenby Avenue                           1                  1      1   
Alma Street                              1                  1      1   
Alpine Avenue                            2                  2      2   
Amanda Street                            1                  1      1   
Ambrose Avenue                           1                  1      1   
Amy Lane                                 9                  9      9   
Ancaster Street East                     3                  3      3   
Anchor Road                              2                  2      2   
Andria Lane                             10                 10     10   
Anjou Place                              1                  1      1   
Ann Street                               2                  2      2   
Apex Court                               1                  1      1   
Apple Drive                              7                  7      7   
Apple Place                              6                  6      6   
Aquasanta Crescent                       1                  1      1   
Arbour Road                              2                  2      2   
Archibald Street                         4                  4      4   
Argyle Avenue                            3                  3      3   
Aries Court                              1                  1      1   
Arkell Street                            1                  1      1   
Arkledun Avenue                          1                  1      1   
Arlington Road                           2                  2      2   
Armstrong Avenue                         1                  1      1   
Arno Street                              1                  1     

In [19]:
# Let us also examine the amount of unique venues that can be curated from all the venues returned and display them
print('There are {} unique categories'. format(len(hamilton_Venues['Category'].unique())))
print(hamilton_Venues['Category'].unique())

There are 19 unique categories
['Automotive Shop' 'Auto Workshop' 'Auto Dealership' 'Locksmith'
 'Auto Garage' 'Hardware Store' None 'Car Wash' 'Auditorium' 'Shoe Repair'
 'Urgent Care Center' 'Electronics Store' 'College Engineering Building'
 'Jewelry Store' 'Dry Cleaner' 'Building' 'Design Studio'
 'Insurance Office' 'Office']


# Step 3: Analyze each address

In [20]:
# one hot encoding
hamiltonVenues_onehot = pd.get_dummies(hamilton_Venues[['Category']], prefix = " ", prefix_sep = " ")
# add the address column to the above created dataframe
hamiltonVenues_onehot['Address'] = hamilton_Venues['Address']
# Let us move the address column to the first column
fixed_columns = [hamiltonVenues_onehot.columns[-1] ] + list (hamiltonVenues_onehot.columns[:-1] )
hamiltonVenues_onehot = hamiltonVenues_onehot[fixed_columns]

print(hamiltonVenues_onehot.shape)
hamiltonVenues_onehot.head()
                                                                 

(3215, 19)


Address    Auditorium    Auto Dealership    Auto Garage  \
0      Abbot Court             0                  0              0   
1      Abbot Court             0                  0              0   
2      Abbot Drive             0                  0              0   
3      Abbot Drive             0                  0              0   
4  Aberdeen Avenue             0                  0              0   

     Auto Workshop    Automotive Shop    Building    Car Wash  \
0                0                  1           0           0   
1                0                  1           0           0   
2                0                  1           0           0   
3                0                  1           0           0   
4                0                  1           0           0   

     College Engineering Building    Design Studio    Dry Cleaner  \
0                               0                0              0   
1                               0                0              0   
2                               0                0              0   
3                               0                0              0   
4                               0                0              0   

     Electronics Store    Hardware Store    Insurance Office    Jewelry Store  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

     Locksmith    Office    Shoe Repair    Urgent Care Center  
0            0         0              0                     0  
1            0         0              0                     0  
2            0         0              0                     0  
3            0         0              0                     0  
4            0         0              0                     0

In [21]:
# Let us group rows by address and by taking the mean of the frequency of the occurence of each category
hamiltonVenues_grouped = hamiltonVenues_onehot.groupby('Address').mean(). reset_index()
hamiltonVenues_grouped

Address    Auditorium    Auto Dealership  \
0                  Abbot Court      0.000000           0.000000   
1                  Abbot Drive      0.000000           0.000000   
2              Aberdeen Avenue      0.000000           0.000000   
3               Academy Street      0.000000           0.000000   
4               Ackland Street      0.000000           1.000000   
5                 Acorn Street      0.000000           0.000000   
6           Adair Avenue South      0.000000           0.000000   
7                 Adams Street      0.000000           0.000000   
8               Adeline Avenue      0.000000           0.000000   
9                 Adler Avenue      0.000000           0.166667   
10               Admiral Place      0.000000           0.000000   
11                 Adorn Court      0.000000           0.000000   
12          Adriatic Boulevard      0.000000           0.000000   
13            Agincourt Avenue      0.000000           0.000000   
14                Agnes Street      0.000000           0.000000   
15               Aikman Avenue      0.000000           0.000000   
16               Aintree Court      0.000000           0.000000   
17              Airdrie Avenue      0.000000           0.000000   
18              Alanson Street      0.500000           0.000000   
19               Albany Avenue      0.000000           0.333333   
20            Albemarle Street      0.000000           0.000000   
21               Albert Street      0.000000           0.000000   
22      Albion Falls Boulevard      0.000000           0.000000   
23           Aldercrest Avenue      0.000000           0.000000   
24            Alexander Street      0.000000           0.000000   
25            Algonquin Avenue      0.000000           0.000000   
26                Alice Street      0.000000           0.000000   
27                Allan Avenue      0.000000           0.125000   
28            Allandale Street      0.000000           0.000000   
29               Allegro Place      0.000000           0.000000   
30              Allenby Avenue      0.000000           0.000000   
31                 Alma Street      0.000000           0.000000   
32               Alpine Avenue      0.500000           0.000000   
33               Amanda Street      0.000000           0.000000   
34              Ambrose Avenue      0.000000           0.000000   
35                    Amy Lane      0.000000           0.111111   
36        Ancaster Street East      0.000000           0.000000   
37                 Anchor Road      0.000000           0.000000   
38                 Andria Lane      0.000000           0.100000   
39                 Anjou Place      0.000000           0.000000   
40                  Ann Street      0.000000           0.000000   
41                  Apex Court      0.000000           1.000000   
42                 Apple Drive      0.000000           0.000000   
43                 Apple Place      0.000000           0.000000   
44          Aquasanta Crescent      0.000000           0.000000   
45                 Arbour Road      0.000000           0.000000   
46            Archibald Street      0.000000           0.000000   
47               Argyle Avenue      0.000000           0.000000   
48                 Aries Court      0.000000           0.000000   
49               Arkell Street      0.000000           0.000000   
50             Arkledun Avenue      0.000000           0.000000   
51              Arlington Road      0.000000           0.000000   
52            Armstrong Avenue      0.000000           0.000000   
53                 Arno Street      0.000000           0.000000   
54         Arthur Avenue North      0.000000           0.000000   
55         Arthur Avenue South      0.000000           0.000000   
56          Artistic Boulevard      0.000000           0.000000   
57                Arvin Avenue      0.000000           0.000000   
58                Ascoli Drive      0.000000           0.000000   
59 

In [22]:
# Now we will print each address along with the top 5 most common enues

num_top_venues = 5
for address_info in hamiltonVenues_grouped['Address']:
    print("----"+address_info+"------")
    temp = hamiltonVenues_grouped[hamiltonVenues_grouped['Address'] == address_info].T.reset_index()
    temp.columns =['venue','freq']
    temp = temp.iloc[1:]
    temp['freq']= temp['freq'].astype(float)
    temp = temp.round({'freq':2})
    print(temp.sort_values('freq', ascending= False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abbot Court------
                 venue  freq
0      Automotive Shop   1.0
1           Auditorium   0.0
2    Electronics Store   0.0
3          Shoe Repair   0.0
4               Office   0.0


----Abbot Drive------
                 venue  freq
0      Automotive Shop   1.0
1           Auditorium   0.0
2    Electronics Store   0.0
3          Shoe Repair   0.0
4               Office   0.0


----Aberdeen Avenue------
                 venue  freq
0      Automotive Shop  0.67
1        Auto Workshop  0.33
2           Auditorium  0.00
3    Electronics Store  0.00
4          Shoe Repair  0.00


----Academy Street------
                 venue  freq
0        Auto Workshop   1.0
1           Auditorium   0.0
2    Electronics Store   0.0
3          Shoe Repair   0.0
4               Office   0.0


----Ackland Street------
               venue  freq
0    Auto Dealership   1.0
1         Auditorium   0.0
2        Shoe Repair   0.0
3             Office   0.0
4          Locksmith   0.0


----Acorn St

In [23]:
# We also will create dataframe for the above results
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending = False)
    
    return  row_categories_sorted.index.values[0:num_top_venues]

In [24]:
num_top_venues = 5
indicators = ['st','nd','rd']
columns = ['Address']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'. format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'. format(ind+1))
        
# Create dataframe

hamilton_venues_sorted = pd.DataFrame(columns=columns)
hamilton_venues_sorted['Address']= hamiltonVenues_grouped['Address']

for ind in np.arange(hamiltonVenues_grouped.shape[0]):
    hamilton_venues_sorted.iloc[ind, 1:] = return_most_common_venues(hamiltonVenues_grouped.iloc[ind,:], num_top_venues)
    
hamilton_venues_sorted.head()

Address 1st Most Common Venue 2nd Most Common Venue  \
0      Abbot Court       Automotive Shop    Urgent Care Center   
1      Abbot Drive       Automotive Shop    Urgent Care Center   
2  Aberdeen Avenue       Automotive Shop         Auto Workshop   
3   Academy Street         Auto Workshop    Urgent Care Center   
4   Ackland Street       Auto Dealership    Urgent Care Center   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0           Shoe Repair       Auto Dealership           Auto Garage  
1           Shoe Repair       Auto Dealership           Auto Garage  
2    Urgent Care Center           Shoe Repair       Auto Dealership  
3           Shoe Repair       Auto Dealership           Auto Garage  
4           Shoe Repair           Auto Garage         Auto Workshop

# Cluster Addresses in Hamilton using Kmeans

In [25]:
# Let us perform clustering analysis
kclusters = 3
hamiltonVenues_grouped_clustering = hamiltonVenues_grouped. drop('Address',1)

kmeans = KMeans(n_clusters = kclusters, random_state =0). fit(hamiltonVenues_grouped_clustering)

hamilton_venues_sorted.insert(0,'Cluster Labels', kmeans.labels_)
hamilton_venues_sorted.head()

Cluster Labels          Address 1st Most Common Venue  \
0               1      Abbot Court       Automotive Shop   
1               1      Abbot Drive       Automotive Shop   
2               1  Aberdeen Avenue       Automotive Shop   
3               0   Academy Street         Auto Workshop   
4               0   Ackland Street       Auto Dealership   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0    Urgent Care Center           Shoe Repair       Auto Dealership   
1    Urgent Care Center           Shoe Repair       Auto Dealership   
2         Auto Workshop    Urgent Care Center           Shoe Repair   
3    Urgent Care Center           Shoe Repair       Auto Dealership   
4    Urgent Care Center           Shoe Repair           Auto Garage   

  5th Most Common Venue  
0           Auto Garage  
1           Auto Garage  
2       Auto Dealership  
3           Auto Garage  
4         Auto Workshop

In [26]:
# I create a new dataframe that includes the cluster as well as the top three venues of each address

hamilton_merged = df
hamilton_merged = hamilton_merged.join(hamilton_venues_sorted.set_index('Address'), on= 'Address')
hamilton_merged.head(5)

Address    Community     ID  Longitude   Latitude  \
0  3rd Concession Road East  Flamborough  63379 -79.860544  43.346062   
1               Abbey Close     Ancaster   4821 -80.001446  43.211121   
2           Abbington Drive     Hamilton   3128 -79.905134  43.228994   
3               Abbot Court     Hamilton  28830 -79.858676  43.223276   
4               Abbot Drive     Hamilton  11971 -79.857134  43.225534   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             NaN                   NaN                   NaN   
1             NaN                   NaN                   NaN   
2             NaN                   NaN                   NaN   
3             1.0       Automotive Shop    Urgent Care Center   
4             1.0       Automotive Shop    Urgent Care Center   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0                   NaN                   NaN                   NaN  
1                   NaN                   NaN                   NaN  
2                   NaN                   NaN                   NaN  
3           Shoe Repair       Auto Dealership           Auto Garage  
4           Shoe Repair       Auto Dealership           Auto Garage

In [27]:
#Let us examine combined dataframe
hamilton_merged.dropna(axis=0, how='any', thresh=None, inplace=True)
hamilton_merged.head(5)

Address  Community     ID  Longitude   Latitude  Cluster Labels  \
3       Abbot Court   Hamilton  28830 -79.858676  43.223276             1.0   
4       Abbot Drive   Hamilton  11971 -79.857134  43.225534             1.0   
7   Aberdeen Avenue  Glanbrook  13465 -79.921113  43.153490             1.0   
8   Aberdeen Avenue   Hamilton    426 -79.888410  43.249750             1.0   
11   Academy Street   Ancaster   8379 -79.974561  43.228072             0.0   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
3        Automotive Shop    Urgent Care Center           Shoe Repair   
4        Automotive Shop    Urgent Care Center           Shoe Repair   
7        Automotive Shop         Auto Workshop    Urgent Care Center   
8        Automotive Shop         Auto Workshop    Urgent Care Center   
11         Auto Workshop    Urgent Care Center           Shoe Repair   

   4th Most Common Venue 5th Most Common Venue  
3        Auto Dealership           Auto Garage  
4        Auto Dealership           Auto Garage  
7            Shoe Repair       Auto Dealership  
8            Shoe Repair       Auto Dealership  
11       Auto Dealership           Auto Garage

In [28]:
# Let's visualize the resulting clusters
map_clusters = folium.Map(location = [latitude,longitude], zoom_start = 11)
x = np.arange(kclusters)
ys = [i + x + (i * x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0,1,len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

#add markers
markers_colors = []
for lat, lon,poi, cluster in zip(hamilton_merged['Latitude'][0:500],  hamilton_merged['Longitude'][0:500],hamilton_merged['Address'][0:500], hamilton_merged['Cluster Labels'][0:500] ):
    label = folium.Popup('Cluster'+ str(cluster), parse_html = True)
    folium.CircleMarker([lat,lon], radius = 5, popup=label, color = rainbow[int(cluster)-1] , fill = True, fill_color = rainbow[int(cluster)-1] ,fill_opacity = 0.7).add_to(map_clusters)
    
map_clusters

In [29]:
# Examine Cluster 1
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 0, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels           1st Most Common Venue  \
11        Ancaster             0.0                   Auto Workshop   
13    Stoney Creek             0.0                 Auto Dealership   
27    Stoney Creek             0.0              Urgent Care Center   
40        Hamilton             0.0                      Auditorium   
42        Hamilton             0.0                 Auto Dealership   
44          Dundas             0.0                   Auto Workshop   
45     Flamborough             0.0                   Auto Workshop   
46        Hamilton             0.0                   Auto Workshop   
48        Hamilton             0.0              Urgent Care Center   
72        Hamilton             0.0                 Automotive Shop   
74          Dundas             0.0                 Automotive Shop   
75        Hamilton             0.0                 Automotive Shop   
77        Hamilton             0.0                 Automotive Shop   
78        Hamilton             0.0                     Auto Garage   
82          Dundas             0.0              Urgent Care Center   
122   Stoney Creek             0.0                 Auto Dealership   
144       Hamilton             0.0                 Automotive Shop   
149       Hamilton             0.0              Urgent Care Center   
150       Hamilton             0.0    College Engineering Building   
162       Hamilton             0.0              Urgent Care Center   
188   Stoney Creek             0.0                 Auto Dealership   
192   Stoney Creek             0.0                   Auto Workshop   
197   Stoney Creek             0.0                 Auto Dealership   
212   Stoney Creek             0.0                 Auto Dealership   
214       Hamilton             0.0                     Auto Garage   
233   Stoney Creek             0.0                   Auto Workshop   
241       Hamilton             0.0                 Auto Dealership   
270       Hamilton             0.0                   Jewelry Store   
272       Hamilton             0.0                   Jewelry Store   
290       Hamilton             0.0                   Auto Workshop   
308       Hamilton             0.0                   Auto Workshop   
315       Hamilton             0.0                     Auto Garage   
317       Hamilton             0.0                     Auto Garage   
336       Hamilton             0.0              Urgent Care Center   
353   Stoney Creek             0.0                 Auto Dealership   
356    Flamborough             0.0                 Automotive Shop   
364   Stoney Creek             0.0                 Auto Dealership   
365   Stoney Creek             0.0                 Auto Dealership   
370       Hamilton             0.0                 Auto Dealership   
374       Ancaster             0.0                        Building   
392   Stoney Creek             0.0                 Auto Dealership   
396       Hamilton             0.0                     Auto Garage   
403       Hamilton             0.0                   Auto Workshop   
406       Hamilton             0.0                      Auditorium   
407       Hamilton             0.0                   Auto Workshop   
444   Stoney Creek             0.0                 Auto Dealership   
453       Hamilton             0.0                 Auto Dealership   
474       Hamilton             0.0                     Auto Garage   
475   Stoney Creek             0.0                 Auto Dealership   
483       Hamilton             0.0                 Auto Dealership   
488       Ancaster             0.0                   Auto Workshop   
495       Hamilton             0.0                   Design Studio   
500       Ancaster             0.0                   Auto Workshop   
505       Ancaster             0.0                   Auto Workshop   
510       Hamilton             0.0                   Auto Workshop   
516         Dundas             0.0                   Auto Workshop   
517       Hamilton 

In [30]:
# Examine Cluster 2
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 1, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
3         Hamilton             1.0       Automotive Shop   
4         Hamilton             1.0       Automotive Shop   
7        Glanbrook             1.0       Automotive Shop   
8         Hamilton             1.0       Automotive Shop   
18        Hamilton             1.0       Automotive Shop   
22        Hamilton             1.0       Automotive Shop   
24        Hamilton             1.0       Automotive Shop   
25        Hamilton             1.0       Automotive Shop   
26        Hamilton             1.0       Automotive Shop   
30        Hamilton             1.0       Automotive Shop   
31        Hamilton             1.0       Automotive Shop   
36        Hamilton             1.0       Automotive Shop   
37        Hamilton             1.0       Automotive Shop   
43        Hamilton             1.0       Automotive Shop   
53       Glanbrook             1.0       Automotive Shop   
54        Hamilton             1.0       Automotive Shop   
64        Hamilton             1.0       Automotive Shop   
69        Ancaster             1.0       Automotive Shop   
70     Flamborough             1.0       Automotive Shop   
83        Hamilton             1.0            Auditorium   
84    Stoney Creek             1.0            Auditorium   
95        Hamilton             1.0       Automotive Shop   
100       Hamilton             1.0       Automotive Shop   
101         Dundas             1.0       Automotive Shop   
102       Hamilton             1.0       Automotive Shop   
105       Hamilton             1.0       Automotive Shop   
110   Stoney Creek             1.0       Automotive Shop   
111         Dundas             1.0       Automotive Shop   
125   Stoney Creek             1.0       Automotive Shop   
126   Stoney Creek             1.0       Automotive Shop   
137       Hamilton             1.0       Automotive Shop   
139       Hamilton             1.0       Automotive Shop   
148       Hamilton             1.0       Automotive Shop   
151       Hamilton             1.0       Automotive Shop   
152       Hamilton             1.0       Automotive Shop   
154       Hamilton             1.0       Automotive Shop   
156       Hamilton             1.0       Automotive Shop   
163   Stoney Creek             1.0       Automotive Shop   
164       Hamilton             1.0       Automotive Shop   
168       Hamilton             1.0       Automotive Shop   
172       Hamilton             1.0       Automotive Shop   
174   Stoney Creek             1.0       Automotive Shop   
182       Hamilton             1.0       Automotive Shop   
193       Hamilton             1.0       Automotive Shop   
195       Hamilton             1.0       Automotive Shop   
198       Hamilton             1.0             Locksmith   
199       Hamilton             1.0       Automotive Shop   
200       Hamilton             1.0       Automotive Shop   
202   Stoney Creek             1.0       Automotive Shop   
208       Hamilton             1.0       Automotive Shop   
211       Hamilton             1.0       Automotive Shop   
215    Flamborough             1.0       Automotive Shop   
218       Hamilton             1.0             Locksmith   
226       Hamilton             1.0       Automotive Shop   
228       Hamilton             1.0       Automotive Shop   
229       Hamilton             1.0       Automotive Shop   
231       Hamilton             1.0       Automotive Shop   
238       Hamilton             1.0       Automotive Shop   
243       Hamilton             1.0       Automotive Shop   
244       Hamilton             1.0       Automotive Shop   
245       Hamilton             1.0       Automotive Shop   
248       Hamilton             1.0       Automotive Shop   
249       Hamilton             1.0       Automotive Shop   
253    Flamborough             1.0       Automotive Shop   
254   Stoney Creek             1.0       Automotive Shop   
255       Hamilton             1.0       Automoti

In [31]:
# Examine Cluster 3
hamilton_merged.loc[hamilton_merged['Cluster Labels'] == 2, hamilton_merged.columns[ [1] + list(range(5, hamilton_merged.shape[1]))]]

Community  Cluster Labels 1st Most Common Venue  \
14        Hamilton             2.0             Locksmith   
19        Hamilton             2.0           Auto Garage   
32        Hamilton             2.0             Locksmith   
79        Hamilton             2.0           Auto Garage   
88        Hamilton             2.0           Auto Garage   
160       Hamilton             2.0           Auto Garage   
161       Hamilton             2.0             Locksmith   
184       Hamilton             2.0           Auto Garage   
203       Hamilton             2.0             Locksmith   
221         Dundas             2.0           Auto Garage   
279       Hamilton             2.0           Auto Garage   
280       Hamilton             2.0           Auto Garage   
368       Hamilton             2.0           Auto Garage   
382       Hamilton             2.0           Auto Garage   
455       Hamilton             2.0           Auto Garage   
499    Flamborough             2.0           Auto Garage   
503       Ancaster             2.0           Auto Garage   
538       Hamilton             2.0             Locksmith   
541       Hamilton             2.0           Auto Garage   
553       Hamilton             2.0           Auto Garage   
559         Dundas             2.0           Auto Garage   
562       Hamilton             2.0           Auto Garage   
572         Dundas             2.0           Auto Garage   
588       Hamilton             2.0           Auto Garage   
615       Hamilton             2.0           Auto Garage   
619         Dundas             2.0           Auto Garage   
629       Hamilton             2.0           Auto Garage   
635       Hamilton             2.0           Auto Garage   
673       Ancaster             2.0           Auto Garage   
676       Hamilton             2.0           Auto Garage   
679       Ancaster             2.0           Auto Garage   
699       Hamilton             2.0           Auto Garage   
701       Hamilton             2.0           Auto Garage   
744       Hamilton             2.0           Auto Garage   
745    Flamborough             2.0           Auto Garage   
746   Stoney Creek             2.0           Auto Garage   
749       Hamilton             2.0           Auto Garage   
750       Hamilton             2.0           Auto Garage   
753       Hamilton             2.0           Auto Garage   
828         Dundas             2.0           Auto Garage   
829    Flamborough             2.0           Auto Garage   
832       Hamilton             2.0       Auto Dealership   
867         Dundas             2.0           Auto Garage   
938    Flamborough             2.0           Auto Garage   
941       Hamilton             2.0           Auto Garage   
972       Hamilton             2.0             Locksmith   
983       Hamilton             2.0           Auto Garage   
1003      Hamilton             2.0           Auto Garage   
1008      Hamilton             2.0       Auto Dealership   
1010      Hamilton             2.0           Auto Garage   
1014        Dundas             2.0           Auto Garage   
1030      Hamilton             2.0           Auto Garage   
1035      Hamilton             2.0           Auto Garage   
1055      Hamilton             2.0           Auto Garage   
1062        Dundas             2.0           Auto Garage   
1077  Stoney Creek             2.0       Auto Dealership   
1088  Stoney Creek             2.0           Auto Garage   
1111      Hamilton             2.0           Auto Garage   
1127      Hamilton             2.0            Auditorium   
1132        Dundas             2.0           Auto Garage   
1152  Stoney Creek             2.0           Auto Garage   
1196        Dundas             2.0           Auto Garage   
1197      Hamilton             2.0           Auto Garage   
1227      Hamilton             2.0           Auto Garage   
1228      Hamilton             2.0           Auto Garage   
1234      Hamilton             2.0           Auto